**Redefining everything from the beginning and separating the df by language of the description**

Definition of a new function that check language

In [0]:
def which_language (text):
    import re
    if bool(re.search('[\u0400-\u04FF]', text)) == True:
        return 'russian'
    else:
        return 'english'

In [0]:
pip install langdetect

In [0]:
pip install goslate

  Created wheel for goslate: filename=goslate-1.5.1-cp36-none-any.whl size=11550 sha256=563b7e6121e157d1c73c603839684ac296153a68c919dcc09ab85878ad0385b0
  Stored in directory: /root/.cache/pip/wheels/4f/7f/28/6f52271012a7649b54b1a7adaae329b4246bbbf9d1e4f6e51a
Successfully built goslate


In [0]:
pip install googletrans

  Created wheel for googletrans: filename=googletrans-2.4.0-cp36-none-any.whl size=15777 sha256=60f5ada0d258a4bdcb9345093f991bebe0a1b94ce7c312f21acbec4c188c78e8
  Stored in directory: /root/.cache/pip/wheels/50/d6/e7/a8efd5f2427d5eb258070048718fa56ee5ac57fd6f53505f95
Successfully built googletrans


In [0]:
import pandas as pd
import numpy as np
from langdetect import detect
import re
import goslate
from googletrans import Translator

### loading two files:
- One file has teams name in Russian and its translation in English
- Second file has leagues name in Russian and its translation in English

In [0]:
teams_names_in_russian_and_english_df = pd.read_csv("teams names in russian and english.csv")
leagues_names_in_russian_and_english_df = pd.read_csv("leagues names in russian and english.csv")

In [0]:
teams_names_in_russian_and_english_df.head(2)

team name in Russian team name in English
0          Санкт-Паули            St. Pauli
1            Рейкьявик            Reykjavik

In [0]:
leagues_names_in_russian_and_english_df.head(2)

leagues name in Russian leagues names in English
0              Чемпионшип             Championship
1            Премьер-лига           Premier League

### Loading the dataset

In [0]:
df = pd.read_csv('result.tar.gz', sep='\t', error_bad_lines=False)

b'Skipping line 37039: expected 12 fields, saw 15\nSkipping line 45611: expected 12 fields, saw 15\n'
b'Skipping line 354339: expected 12 fields, saw 18\nSkipping line 360804: expected 12 fields, saw 102\nSkipping line 360819: expected 12 fields, saw 78\nSkipping line 379126: expected 12 fields, saw 14\nSkipping line 444446: expected 12 fields, saw 16\nSkipping line 449079: expected 12 fields, saw 16\nSkipping line 450250: expected 12 fields, saw 15\n'
b'Skipping line 481374: expected 12 fields, saw 18\nSkipping line 510619: expected 12 fields, saw 20\nSkipping line 512271: expected 12 fields, saw 14\nSkipping line 514317: expected 12 fields, saw 15\nSkipping line 519707: expected 12 fields, saw 40\n'
b'Skipping line 538495: expected 12 fields, saw 13\n'
b'Skipping line 765901: expected 12 fields, saw 56\nSkipping line 773310: expected 12 fields, saw 43\n'
b'Skipping line 805899: expected 12 fields, saw 13\nSkipping line 868492: expected 12 fields, saw 21\nSkipping line 871801: expecte

In [0]:
df = df.drop(["url", "video_url", "source_name", "author_name"], axis=1)

### Rremoving all the URLs from data (noise in data):

In [0]:
df['result.tsv'] = df['result.tsv'].replace(r'http\S+', '', regex=True).replace(r'www\S+', '', regex=True).replace(r'https\S+', '', regex=True)

Replacing any remaining noise from data including missing values, duplicate values and other data abnormality with NaN and then deleting all NaNs:

In [0]:
df = df.replace('', np.NaN)
df = df.replace('\xa0', np.NaN)
df = df.dropna()
df =  df[df['result.tsv'].str.contains('[A-Za-z]')]
df = df[df['result.tsv'].str.split().str.len().gt(1)]

In [0]:
df = df.drop_duplicates()

In [0]:
df = df.reset_index(drop=True)

Loop to create a list of languages of each description

In [0]:
lang=[]
for i,text in enumerate(df['result.tsv'].values): 
    lang.append(which_language(str(text)))

Based on the language list, we add a new column to the dataframe that contain the language of the description

In [0]:
df['Language'] = lang 

Split the dataframe based on the language column

In [0]:
grouped=df.groupby('Language')

**Create two new dataframe, each contain just one language, those groups do not contain the language column**

In [0]:
for name, group in grouped: 
    if name == 'english': 
        english = group.drop('Language',axis=1) 
    else: 
        russian = group.drop('Language',axis=1)

### Joining the dataframes - in order to match the russian name in one dataframe with its corresponding english translation from second dataframe  

In [0]:
english = pd.merge(english, teams_names_in_russian_and_english_df,  how='left', left_on=['team_of_season_1_name_in_russian'], right_on = ['team name in Russian'])
english.rename({'English': 'team_of_season_1_name_in_english'}, axis=1, inplace=True)

english = pd.merge(english, teams_names_in_russian_and_english_df,  how='left', left_on=['team_of_season_2_name_in_russian'], right_on = ['team name in Russian'])
english.rename({'English': 'team_of_season_2_name_in_english'}, axis=1, inplace=True)

english = pd.merge(english, leagues_names_in_russian_and_english_df,  how='left', left_on=['league_name_in_russian'], right_on = ['leagues name in Russian'])
english.rename({'unique_leagues_in_english': 'league_name_in_english'}, axis=1, inplace=True)


In [0]:
# Renaming the columns so one check that what's in it and interpret the information easily 
english.rename({'team name in English_x': 'team_of_season_1_name_in_english'}, axis=1, inplace=True)
english.rename({'team name in English_y': 'team_of_season_2_name_in_english'}, axis=1, inplace=True)
english.rename({'leagues names in English': 'league_name_in_english'}, axis=1, inplace=True)

In [0]:
english.head(2)

result.tsv  ... league_name_in_english
0  Middlesbrough have woken to good times in thei...  ...           Championship
1  Wolves prefer to attack with pace on the count...  ...         Premier League

[2 rows x 14 columns]

In [0]:
english.drop(['team name in Russian_x' , 'team name in Russian_y' , 'leagues name in Russian' ] , axis=1 , inplace=True)

In [0]:
english.head()

result.tsv  ... league_name_in_english
0  Middlesbrough have woken to good times in thei...  ...           Championship
1  Wolves prefer to attack with pace on the count...  ...         Premier League
2  In my opinion a 0-0 draw is quite likely betwe...  ...     UEFA Europa League
3  with home side Valencia having a massive advan...  ...     UEFA Europa League
4  tow side who fill the bottom two places in the...  ...                example

[5 rows x 11 columns]

In [0]:
# setting the correct data type that english names should be string
english['team_of_season_1_name_in_english']=english['team_of_season_1_name_in_english'].astype(str)
english['team_of_season_2_name_in_english']=english['team_of_season_2_name_in_english'].astype(str)
english['league_name_in_english']=english['league_name_in_english'].astype(str)

**Direct_matching the new datasetes:**





**Match on team1**

In [0]:
teams1_match = np.zeros(english.shape[0])

In [0]:
print("Mismatch Values")
print("*************************************************************************")
for i, team1 in enumerate(english['team_of_season_1_name_in_english']):
  if team1 in english['result.tsv'].values[i] :
    teams1_match[i] = 1 
  else:
    print(team1)
    print(english['result.tsv'].values[i])
    print(".......................................................................")
    teams1_match[i] = 0

Streaming output truncated to the last 5000 lines.
Parma
Scored at home to Cagliari and is a winger who likes to cut into the box and have a strike on goal. Torino are not great on the road, fancy Barilla to strike first.
.......................................................................
Stoke City
Not given a hard time yet and only played 58 minutes at Arsenal so i think he may get the start tonight and should be given the chance to registrar his first goal of the season
.......................................................................
Manchester United
The odds look a bit too large for the big German defender the break the deadlock. He scored the first goal in the reverse fixture at the Bridge and he will be a presence at attacking set pieces for the Blues
.......................................................................
Manchester United
This man is back from injury and he has scored a few goals and this is the best long shot option for the first goal and he might g

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
.......................................................................
Seattle Saunders
I can see plenty of goals in this game as Seattle Sounders FC have seen 22 goals scored in their last 6 games and LA Galaxy have seen 21 goals scored in their last 6 games, both teams have been over in 9 of their last 10 games
.......................................................................
Los Angeles FC
LAFC have just been over machines this season and find it difficult to not score more than two goals in every single game they play.
.......................................................................
Los Angeles FC
Both teams are capable of scoring multiple goals and LAFC could probably hit this total all by themselves. Bet of the day.
.......................................................................
Sligo Rovers
Sligo have four games in a row with over 2.5 goals and Dundalk have six. It was 4-0 to Dundalk when they last faced of

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
.......................................................................
Wolverhampton
Wolves have endure a difficult start to the domestic league season but have been rock solid in this tournament so far and their home form last season was excellent. The visitors haven’t kept a clean sheet in any of their last 15 Europa League away matches, and before the international break lost heavily at home to Benfica. Home win.
.......................................................................
Shamrock Rovers
Shamrock in 2nd place and 10 points behind leaders Dundalk so will going all out for 3 points. They have W5 D1 of last 6 home games in all competitions and have only lost twice in their last 18 league games. St Patricks have been in decent form away from home of late winning 4 of their last 5 in the league. They have a fairly tight defence having seen under 2.5 goals in 15 of their last 20 in the league. Verdict: I'm expecting a tight g

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
.......................................................................
Juventus
Last home game for Allegri. With the scudetto already wrapped up this has little meaning for Juve but alot for Atalanta who are challenging for a top 4 position. A draw should satisfy both squads and hence my prediction is an X.
.......................................................................
Napoli
Inter Milan have drawn four of their last six games in the league and another draw here would likely seal a champions league spot.
.......................................................................
Steaua
Both sides are in very good form sitting first and second in the table with very little to separate them. Their last meeting was a draw.
.......................................................................
associação chapecoense de futebol
Both sides are low on confidence having only won one of their last six league games each. Very little betwe

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [0]:
english['direct_match_for_teams1'] = teams1_match

In [0]:
print("The values which are not matched are indicated by 0 and the values which are matched are indicated by 1")
english['direct_match_for_teams1'].value_counts()

The values which are not matched are indicated by 0 and the values which are matched are indicated by 1


0.0    50694
1.0    38571
Name: direct_match_for_teams1, dtype: int64

In [0]:
all_vals = english['direct_match_for_teams1'].shape[0]
success = english[english['direct_match_for_teams1'] == 1].shape[0]
failure = english[english['direct_match_for_teams1'] == 0].shape[0]
print("Total Values are: ",all_vals)
print("Total success/matched values are: ",success)
print("Total failed/mis-matched values are: ",failure)

Total Values are:  89265
Total success/matched values are:  38571
Total failed/mis-matched values are:  50694


In [0]:
baseline_team1 = success / all_vals
print("Result value is: ",baseline_team1)
print("Result value in percentage is: ",baseline_team1*100 , "%")

Result value is:  0.4320954461435053
Result value in percentage is:  43.209544614350534 %


**Match on team2**

In [0]:
teams2_match = np.zeros(english.shape[0])

In [0]:
print("Mismatch Values")
print("*************************************************************************")
for i, team2 in enumerate(english['team_of_season_2_name_in_english']):
  if team2 in english['result.tsv'].values[i] :
    teams2_match[i] = 1 
  else: 
    print(team2)
    print(english['result.tsv'].values[i])
    print(".......................................................................")
    teams2_match[i] = 0

Streaming output truncated to the last 5000 lines.
.......................................................................
Glasgow Rangers
Rangers have improved in comparison to past seasons and I think they stand good chances for a result tonight in Denmark. At least I would expect them to score a goal, the scorer of which most likely will be Morelos as usual.
.......................................................................
Glasgow Rangers
Manager Steven Gerrard knows what it takes to win these European games, and he will have instructed his best player, Alfredo Morelos to get in the right positions
.......................................................................
FC Midtjylland
Steve Gerrard as fielded a strong team tonight, and Alfredo Morelos is the best player in the side, he will be thereabouts when the goals come
.......................................................................
Glasgow Rangers
Alfredo Morelos scored 3 goals against Midtjylland (in both legs) i

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
These two sides met last time out a couple of weeks ago in the Championship, the game ended 2-1, Cardiff's 2 home games this season have all been both teams scoring and over 2.5, Luton 2 of 3 away games have been both teams scoring and over 2.5 goals.
.......................................................................
Stoke City
These two sides have met already this season, Leeds won 3-0. Last two meetings before that saw both teams scoring and over 2.5 goals. Leeds have scored in their last 6 games. Stoke have scored in their last 5 of 6 games.
.......................................................................
Dinamo Zagreb
Early goal for Dinamo and two goals lead at the first match. Rozenborg is strong in their home i expect early goal. Mt tip is over 2,5 goals.
.......................................................................
Carlisle United
3 of 4 Rochdale's home games have been over 2.5 goals, Rochdale have scored (

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
Mainz
Bayern are a better side 
.......................................................................
Brescia
Milan have a good team 
.......................................................................
Sheffield United
Chelsea did not start the season the best, so today they will do everything to win a first home game
.......................................................................
Tottenham Hotspur
Arsenal are a better side 
.......................................................................
Barrow
Woking to win this home game. They are the leader of the championship and also have 5 straight wins. They didn’t take victory over this opponent since 2012 and it is time to change that.
.......................................................................
Sheffield United
Chelsea just won their first game a 3-2 on the road against Norwich and they looked pretty good. Sheff Utd lost here against Leicester so i see Chelsea

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
.......................................................................
den Haag
Den Haag won this clash last season 0-2 when Feyenoord were looking a much better side. They have 6 points each and I think the surprise can replicate since hosts are already -7 points from the top. Feyenoord are a big club and will score however.
.......................................................................
Wings of Soviets
Samara leads the direct fight with 5W-2D in 9 direct developments. In fact, Samara was clear when he played a match with Krasnodar, succeeling every time (when they won) to score between 2 and 3 goals, the results being: 1-2, 1-3, 0-3, 0-2 and 1-2. That is why I think Samara can win for the 6th time, and Krasnodar (I hope) mark it, because Samara can close very well on the defensive.
.......................................................................
Marseilles
Monaco escaped relegation last season by the skin of their te

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Manchester in much better shape. 
.......................................................................
Copenhagen
Kipengagen win
.......................................................................
PSV
Psv must do it
.......................................................................
RB Leipzig
Leipzig win
.......................................................................
Leicester City
Foxes should perform well
.......................................................................
Arsenal
Chunki arsenal kamida durrang uynaydi
.......................................................................
Genoa
olanak sağlamaktadır.[14] Türkiye Türkçesi bu yönünden dolayı diğer Türk dilleriyle ortak ya da ayrık bulunan onlarca eke sahiptir.[15] Türkçe geniş kullanımıyla birlikte zengin bir dil
.......................................................................
Marseilles
v etoi vstre4e javnim favoritom s4itau komandu Marsel kotoraja sa poslednie pjat mat4ei o4nix vstre4 ode

In [0]:
english['direct_match_for_teams2'] = teams2_match

In [0]:
print("The values which are not matched are indicated by 0 and the values which are matched are indicated by 1")

english['direct_match_for_teams2'].value_counts()

The values which are not matched are indicated by 0 and the values which are matched are indicated by 1


0.0    52149
1.0    37116
Name: direct_match_for_teams2, dtype: int64

In [0]:
success2 = english[english['direct_match_for_teams2'] == 1].shape[0]
failure2 = english[english['direct_match_for_teams2'] == 0].shape[0]
print("Total Values are: ",all_vals)
print("Total success/matched values are: ",success2)
print("Total failed/mis-matched values are: ",failure2)

Total Values are:  89265
Total success/matched values are:  37116
Total failed/mis-matched values are:  52149


In [0]:
baseline_team2 = success2 / all_vals
print("Result value is: ",baseline_team2)
print("Result value in percentage is: ",baseline_team2*100 , "%")

Result value is:  0.4157956645941859
Result value in percentage is:  41.57956645941859 %


**Match by league**

In [0]:
leagues_match = np.zeros(english.shape[0])

In [0]:
print("Mismatch Values")
print("*************************************************************************")
for i, league in enumerate(english['league_name_in_english']):
  if league in english['result.tsv'].values[i] :
    leagues_match[i] = 1 
  else: 
    print(league)
    print(english['result.tsv'].values[i])
    print(".......................................................................")
    leagues_match[i] = 0

Streaming output truncated to the last 5000 lines.
Oppose both teams to score in this one. Salford have been a fast improving side and their home form last season was very strong. They can keep a clean sheet here.
.......................................................................
MLS
Atlanta United are a very strong side at home and are deservedly strong favourites here. LA Galaxy are likely to get few chances in this game and so both teams to score is opposed.
.......................................................................
J-League
The Kawasaki defence were very band in the last round and they got 3 goals. Now I think both teams will not score.
.......................................................................
Superbowl
Oppose both teams to score here. Liverpool looked a little shaky in pre-season and Man City are still the dominant side in my opinion. They can keep a clean sheet here.
.......................................................................
Championsh

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
.......................................................................
UEFA Europa League
Espanyol made very light work of qualifying while Ferencvaros made it despite winning just one of four games. In Spain on their return to European competition Espanol are fancied to win with plenty in hand and can cover the -1.25 handicap.
.......................................................................
UEFA Europa League
Borussia Monchengladbach owns a lot valued at 257 million euros, and the cumulative value of Wolfsberger's players is 11.65 million euros, according to transfermarkt.ro. The Austrians benefit from a single player whose 6-digit odds (Weissman - 1 million), while the Germans have only two odds below one million, while Ginter is valued at 35 million, and Plea and Rise to 30 million! This difference in value should speak its way, associated with the difference in international experience. I bet on a clear victory of the home 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
In last three home matches of Linfield Belfast team were scored 15 goals. In last three away matches of Karabakh Agdam team were scored 6 goals.
.......................................................................
UEFA Europa League
In last three home matches of RCD Espanyol team were scored 9 goals. In last three away matches of Zorya Lugansk team were scored 7 goals.
.......................................................................
UEFA Europa League
Guimaraes have four points from six this season in Portugal and they had a very good pre season campaign. Steaua are decent at home and I can see both teams scoring as the Portuguese side will fancy themselves to score away. Going over 2.5 goals in this first leg in Romania.
.......................................................................
UEFA Europa League
Both teams capable of scoring goals. They show in last round that after Braga scored 7 goals in two games against Br

...

Streaming output truncated to the last 5000 lines.
.......................................................................
Championship
Neither side have been in great form Wigan have 1 win 2 draws and 2 defeats from their last 5 league games. Birmingham have won 2 and lost 3 of their last 5 league games and were beaten in 3 of their last 4 away games. Wigan have won 2 drawn 1 and lost 1 of their home games to date. On the balance of form predicting a home win.
.......................................................................
UEFA Champions League
Real Madrid lost their first group game away to PSG so have some catching up to do. They should prove to skillful for Club Brugge who drew their first game 0-0 at home to Galatasaray
.......................................................................
UEFA Champions League
Leverkusen have had a reasonable start this season in Germany, but their away form is not as strong as at home with a draw and a defeat already in 3 matches in the

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
Man City and Shakhtar were in the same group in previous two tournaments. Man City easily won 3 of 4 games with 6-0, 3-0 and 2-0 scores. And lost 1 game, that they didn't care about, with their backups and youngsters. Oblviously, Man City wants to start with a win and bounce back from a loss to Norwich. 0-3 here.
.......................................................................
UEFA Champions League
Inter Milan are on top of their domestic competition. However,they have not won any of their last four matches in this competition. Slavia Prague have won six of their last seven competitive matches and have won their last two matches in this competition.
.......................................................................
Allsvenskan
AFC Eskilstuna have lost their last matches and in the last three against Elfsborg they lost the lot. Elfsborg have won three in four and I am tipping them to win today.
..............................

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
.......................................................................
Ligue 1
These two teams are split by just 2 points as they are very equally matched.Harmannstadt has been very decent at home with 3 wins in 4 games with both teams scoring in 3 of them as well.On other hand Botosani has managed to both score and concede in 8 of their 10 matches with 6 of those 8 games finishing in a draw so got to fancy another draw with goals in this one.
.......................................................................
series B
Juve Stabia has been playing very poorly and Citadella is also doing quite poorly on the road with 2 easy losses so this should make for very close game.They drew last 2 times Juve stabia hosted their hth matches with both draws seeing goals so got to like this price on BTTS and draw alongside it.
.......................................................................
series B
Both Venezia and Pisa started the seaso

In [0]:
english['direct_match_for_leagues'] = leagues_match

In [0]:
print("The values which are not matched are indicated by 0 and the values which are matched are indicated by 1")
english['direct_match_for_leagues'].value_counts()

The values which are not matched are indicated by 0 and the values which are matched are indicated by 1


0.0    85721
1.0     3544
Name: direct_match_for_leagues, dtype: int64

In [0]:
failure_l = english[english['direct_match_for_leagues'] == 0].shape[0]
success_l = english[english['direct_match_for_leagues'] == 1].shape[0]
print("Total Values are: ",all_vals)
print("Total success/matched values are: ",success_l)
print("Total failed/mis-matched values are: ",failure_l)

Total Values are:  89265
Total success/matched values are:  3544
Total failed/mis-matched values are:  85721


In [0]:
baseline_league = success_l / all_vals
print("Result value is: ",baseline_league)
print("Result value in percentage is: ",baseline_league*100 , "%")

Result value is:  0.03970201086652103
Result value in percentage is:  3.970201086652103 %


**Match by Bookmaker**

In [0]:
bookmaker_match = np.zeros(english.shape[0])

In [0]:
for i, bookmaker in enumerate(english['bookmaker_name']):
  if bookmaker in english['result.tsv'].values[i] :
    bookmaker_match[i] = 1 
  else: 
    bookmaker_match[i] = 0

In [0]:
english['direct_match_for_bookmakers'] = bookmaker_match

In [0]:
print("The values which are not matched are indicated by 0 and the values which are matched are indicated by 1")
english['direct_match_for_bookmakers'].value_counts()

The values which are not matched are indicated by 0 and the values which are matched are indicated by 1


0.0    89261
1.0        4
Name: direct_match_for_bookmakers, dtype: int64

In [0]:
success_b = english[english['direct_match_for_bookmakers'] == 1].shape[0]
failure_b = english[english['direct_match_for_bookmakers'] == 0].shape[0]
print("Total Values are: ",all_vals)
print("Total success/matched values are: ",success_b)
print("Total failed/mis-matched values are: ",failure_b)

Total Values are:  89265
Total success/matched values are:  4
Total failed/mis-matched values are:  89261


In [0]:
baseline_bookmaker = success_b / all_vals
print("Result value is: ",baseline_bookmaker)
print("Result value in percentage is: ",baseline_bookmaker*100 , "%")

Result value is:  4.4810396011874754e-05
Result value in percentage is:  0.004481039601187476 %


**Match by coefficients (odd):**

In [0]:
odd_match = np.zeros(english.shape[0])

In [0]:
for i, odd in enumerate(english['odd']):
  if str(odd) in english['result.tsv'].values[i]:
    odd_match[i] = int(1) 
  else:
    odd_match[i] = int(0)

In [0]:
english['direct_match_for_odds'] = odd_match

In [0]:
print("The values which are not matched are indicated by 0 and the values which are matched are indicated by 1")
english['direct_match_for_odds'].value_counts()

The values which are not matched are indicated by 0 and the values which are matched are indicated by 1


0.0    87375
1.0     1890
Name: direct_match_for_odds, dtype: int64

In [0]:
success_c = english[english['direct_match_for_odds'] == 1].shape[0]
failure_c = english[english['direct_match_for_odds'] == 0].shape[0]
print("Total Values are: ",all_vals)
print("Total success/matched values are: ",success_c)
print("Total failed/mis-matched values are: ",failure_c)

Total Values are:  89265
Total success/matched values are:  1890
Total failed/mis-matched values are:  87375


In [0]:
baseline_odds = success_c / all_vals
print("Result value is: ",baseline_odds)
print("Result value in percentage is: ",baseline_odds*100 , "%")

Result value is:  0.02117291211561082
Result value in percentage is:  2.1172912115610822 %


**Match on tip-name (betting text):**

In [0]:
tip_match = np.zeros(english.shape[0])


In [0]:
for i, tip in enumerate(english['tip_name']):
  if tip in english['result.tsv'].values[i] :
    tip_match[i] = 1 
  else: 
    tip_match[i] = 0

In [0]:
english['direct_match_for_tips'] = tip_match

In [0]:
print("The values which are not matched are indicated by 0 and the values which are matched are indicated by 1")
english['direct_match_for_tips'].value_counts()

The values which are not matched are indicated by 0 and the values which are matched are indicated by 1


0.0    86944
1.0     2321
Name: direct_match_for_tips, dtype: int64

In [0]:
success_t = english[english['direct_match_for_tips'] == 1].shape[0]
failure_t = english[english['direct_match_for_tips'] == 0].shape[0]
print("Total Values are: ",all_vals)
print("Total success/matched values are: ",success_t)
print("Total failed/mis-matched values are: ",failure_t)

Total Values are:  89265
Total success/matched values are:  2321
Total failed/mis-matched values are:  86944


In [0]:
baseline_tips = success_t / all_vals
print("Result value is: ",baseline_tips)
print("Result value in percentage is: ",baseline_tips*100 , "%")

Result value is:  0.026001232285890328
Result value in percentage is:  2.600123228589033 %


**`Match` by date**

In [0]:
date_match = np.zeros(english.shape[0])


In [0]:
for i, date in enumerate(english['match_date_time']):
  if date in english['result.tsv'].values[i] :
    date_match[i] = 1 
  else: 
    date_match[i] = 0

In [0]:
english['direct_match_for_date'] = date_match

In [0]:
print("The values which are not matched are indicated by 0 and the values which are matched are indicated by 1")
english['direct_match_for_date'].value_counts()

The values which are not matched are indicated by 0 and the values which are matched are indicated by 1


0.0    89265
Name: direct_match_for_date, dtype: int64

In [0]:
success_d = english[english['direct_match_for_date'] == 1].shape[0]
failure_d = english[english['direct_match_for_date'] == 0].shape[0]
print("Total Values are: ",all_vals)
print("Total success/matched values are: ",success_d)
print("Total failed/mis-matched values are: ",failure_d)

Total Values are:  89265
Total success/matched values are:  0
Total failed/mis-matched values are:  89265


In [0]:
baseline_date = success_d / all_vals
print("Result value is: ",baseline_date)
print("Result value in percentage is: ",baseline_date*100 , "%")

Result value is:  0.0
Result value in percentage is:  0.0 %


**Dataset with new columns**

In [0]:
english.head(10)

result.tsv  ... direct_match_for_date
0  Middlesbrough have woken to good times in thei...  ...                   0.0
1  Wolves prefer to attack with pace on the count...  ...                   0.0
2  In my opinion a 0-0 draw is quite likely betwe...  ...                   0.0
3  with home side Valencia having a massive advan...  ...                   0.0
4  tow side who fill the bottom two places in the...  ...                   0.0
5  The reverse fixture ended 0-0 and it won't be ...  ...                   0.0
6  These two have conceded a combined nine goals ...  ...                   0.0
7  It would be a surprise if Roar deny Adelaide a...  ...                   0.0
8  Preston have ended the season on a low with 5L...  ...                   0.0
9  A low scoring game is anticipated, Macclesfiel...  ...                   0.0

[10 rows x 18 columns]